In [3]:
# imports
import requests
import json
import pandas as pd
import os

In [4]:
bike_stations_df = pd.read_csv('bike_stations.csv', index_col = 0)

In [3]:
bike_stations_df

Station Name  Available Bikes  Empty Slots  \
0               W 100 St & Manhattan Ave               33            0   
1             7 Ave & Central Park South                5           64   
2                Bedford Ave & Bergen St                4           14   
3                         28 St & 41 Ave                4           18   
4     Frederick Douglass Blvd & W 112 St               32            0   
...                                  ...              ...          ...   
1981       Eastern Pkwy & Washington Ave                3           27   
1982               87 St & Roosevelt Ave                1           22   
1983         Eastern Pkwy & Franklin Ave                2           29   
1984                      34 Ave & 83 St                6           16   
1985                    72 St & Broadway                1           19   

       Latitude  Longitude  
0     40.795000 -73.964500  
1     40.766741 -73.979069  
2     40.676368 -73.952918  
3     40.751047 -73.937970  
4     40.801694 -73.957145  
...         ...        ...  
1981  40.671649 -73.963115  
1982  40.748250 -73.879360  
1983  40.670777 -73.957680  
1984  40.753750 -73.884230  
1985  40.747510 -73.893720  

[1986 rows x 5 columns]

In [5]:
bike_stations1_df = bike_stations_df.iloc[:500]
bike_stations2_df = bike_stations_df.iloc[500:1000]
bike_stations3_df = bike_stations_df.iloc[1000:1500]
bike_stations4_df = bike_stations_df.iloc[1500:]

# Foursquare

Send a request to Foursquare with a small radius (1000m) for all the bike stations in your city of choice. 

In [9]:
def query_foursquare_for_places(lat, lng, radius=1000, limit = 50):
    url = f"https://api.foursquare.com/v3/places/search"
    FOURSQUARE_API_VERSION = '20230820'
    params = {
        'v': FOURSQUARE_API_VERSION,
        'll': f"{lat},{lng}",
        'radius': radius
    }
    
    api_key = 'fsq3IoTPSahhgq2PU0WEA8WgLb9ShifYHJC1AA8ZLrnzXn8='
    
    # Create dictionary for headers
    headers = {"Accept": "application/json"}
    # Add key with our API KEY
    headers['Authorization'] = api_key

    try:
        response = requests.get(url, headers=headers, params=params)
        #print(response)
        #print("Response content:", response.content)  # Print the raw response content
        response_data = response.json()
        #print(response.json())
        
        if 'results' in response_data:
            places = response_data['results']
            return places
        else:
            print("No Place of Interest found")
            return []         

    except requests.exceptions.RequestException as e:
        print("Error making API request:", e)
        return []

In [ ]:
if bike_stations_df is not None:
    for index, row in bike_stations_df.iterrows():
        print(f"Station Name: {row['Station Name']}")
        print(f"Available Bikes: {row['Available Bikes']}")
        print(f"Empty Slots: {row['Empty Slots']}")
        print(f"Latitude: {row['Latitude']}")
        print(f"Longitude: {row['Longitude']}")
        
        query_foursquare_for_places(row['Latitude'], row['Longitude'])

Station Name: W 100 St & Manhattan Ave
Available Bikes: 33
Empty Slots: 0
Latitude: 40.795
Longitude: -73.9645
{'results': [{'fsq_id': '4fdc9a79e4b0735a6deafc25', 'categories': [{'id': 13035, 'name': 'Coffee Shop', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/coffeeshop_', 'suffix': '.png'}}], 'chains': [{'id': 'ab4c54c0-d68a-012e-5619-003048cad9da', 'name': 'Starbucks'}], 'distance': 100, 'geocodes': {'main': {'latitude': 40.795045, 'longitude': -73.965638}, 'roof': {'latitude': 40.795045, 'longitude': -73.965638}}, 'link': '/v3/places/4fdc9a79e4b0735a6deafc25', 'location': {'address': '805 Columbus Ave', 'address_extended': 'Frnt 2', 'census_block': '360610185001000', 'country': 'US', 'cross_street': 'at W 100th St', 'dma': 'New York', 'formatted_address': '805 Columbus Ave (at W 100th St), New York, NY 10025', 'locality': 'New York', 'postcode': '10025', 'region': 'NY'}, 'name': 'Starbucks', 'related_places': {}, 'timezone': 'America/New_York'}, {'fsq_id': '4a95cf

Parse through the response to get the POI (such as restaurants, bars, etc) details you want (ratings, name, location, etc)

In [ ]:
def foursqare_places_of_interest(lat, lng, limit = 50):
    poi = query_foursquare_for_places(lat, lng, radius=1000)
    
    if poi:
        print("Nearby Places of Interest:")
        for places in poi:
            if 'coffee' in places['categories'][0]['name'].lower() or 'restaurant' in places['categories'][0]['name'].lower() or 'bar' in places['categories'][0]['name'].lower() or 'hotel' in places['categories'][0]['name'].lower():
                print(f"Business Category: {places['categories'][0]['name']}")
                if places['chains']:
                    print(f"Business Chain: {places['chains']}")
                print(f"Business Name: {places['name']}")
                print(f"Business Address: {places['location']['formatted_address']}")
                print("-" * 30)
    else:
        print("No Business found")

In [ ]:
if bike_stations_df is not None:
    for index, row in bike_stations_df.iterrows():
        print(f"Station Name: {row['Station Name']}")
        print(f"Available Bikes: {row['Available Bikes']}")
        print(f"Empty Slots: {row['Empty Slots']}")
        print(f"Latitude: {row['Latitude']}")
        print(f"Longitude: {row['Longitude']}")
        
        
        foursqare_places_of_interest(row['Latitude'], row['Longitude'])

Put your parsed results into a DataFrame

In [12]:
business = []

In [13]:
if bike_stations1_df is not None:
    for index, row in bike_stations_df.iterrows():
        results = query_foursquare_for_places(row['Latitude'], row['Longitude'], limit = 50)
        
        for each in results:
            if each['categories']:
                Category = each['categories'][0]['name']
            if each['name']:
                Name = each['name']
            if each['location']:
                Location = each['location']['formatted_address']
            
                      
            if 'coffee' in Category.lower() or 'restaurant' in Category.lower() or 'bar' in Category.lower() or 'hotel' in Category.lower():
                business.append({'Station Name': row['Station Name'], 'Business Category': Category, 'Business Name': Name, 'Address': Location})
foursquare_business_df = pd.DataFrame(business)

In [ ]:
foursquare_business_df = pd.DataFrame(business)

In [14]:
foursquare_business_df

Station Name      Business Category  \
0       W 100 St & Manhattan Ave            Coffee Shop   
1       W 100 St & Manhattan Ave  Vietnamese Restaurant   
2       W 100 St & Manhattan Ave     Italian Restaurant   
3     7 Ave & Central Park South   Brazilian Restaurant   
4     7 Ave & Central Park South     Italian Restaurant   
...                          ...                    ...   
7723            72 St & Broadway   Himalayan Restaurant   
7724            72 St & Broadway    Filipino Restaurant   
7725            72 St & Broadway      Indian Restaurant   
7726            72 St & Broadway      Indian Restaurant   
7727            72 St & Broadway  Vietnamese Restaurant   

               Business Name  \
0                  Starbucks   
1                  Saiguette   
2                Osteria 106   
3              NYAC Tap Room   
4                      Marea   
...                      ...   
7723        Bhanchha Ghar II   
7724                  Ihawan   
7725            Dosa Delight   
7726  Angel Indian Restauran   
7727                Thai Son   

                                                Address  
0     805 Columbus Ave (at W 100th St), New York, NY...  
1     935 Columbus Ave (at W 106th St), New York, NY...  
2     53 W 106th St (Btwn Manhattan and Columbus), N...  
3                                    New York, NY 10019  
4     240 Central Park S (at 59th St & Broadway), Ne...  
...                                                 ...  
7723  7415 Roosevelt Ave (btwn 74th & 75th St), Jack...  
7724  4006 70th St (at Roosevelt Ave), Woodside, NY ...  
7725  3566 73rd St (btw 35th & 37th Ave), Jackson He...  
7726                   7414 37th Rd, New York, NY 11372  
7727    40-10 74TH St (at Broadway), Elmhurst, NY 11373  

[7728 rows x 4 columns]

# Yelp

Send a request to Yelp with a small radius (1000m) for all the bike stations in your city of choice. 

In [15]:
def query_yelp_for_places(lat, lng, radius = 1000, limit = 10):
    url = "https://api.yelp.com/v3/businesses/search"
    api_key = 'o44uACDHdbo-bwEDH7P-Ja0PDgIliS9ErdUH5dZF5Bjj6lagjSBLgARt9Wey9iBa5554J5W2ZDd8iV2kxvFge4DY7iHot2dHH1-WH8WTFJSHT5WQhgwn98myivP3ZHYx'

    params = {
        "latitude": lat,
        "longitude": lng,
        "radius": radius
    }
    
    headers = {
        "Authorization": f"Bearer {api_key}"
    }
    
    try:
        response = requests.get(url, params=params, headers=headers)
        #print(response)
        #print(response.content)
        response_data= response.json()
        
        if 'businesses' in response_data:
            places = response_data['businesses']
            return places
        else:
            print("No Place of Interest found")
            return []
    except requests.exceptions.RequestException as e:
        print("Error making API request:", e)
        return []

In [12]:
if bike_stations_df is not None:
    for index, row in bike_stations_df.iterrows():
        print(f"Station Name: {row['Station Name']}")
        print(f"Available Bikes: {row['Available Bikes']}")
        print(f"Empty Slots: {row['Empty Slots']}")
        print(f"Latitude: {row['Latitude']}")
        print(f"Longitude: {row['Longitude']}")
        
        query_yelp_for_places(row['Latitude'], row['Longitude'])

Station Name: W 100 St & Manhattan Ave
Available Bikes: 33
Empty Slots: 0
Latitude: 40.795
Longitude: -73.9645


NameError: name 'query_yelp_for_places' is not defined

Parse through the response to get the POI (such as restaurants, bars, etc) details you want (ratings, name, location, etc)

In [14]:
def yelp_places_of_interest(lat, lng, limit = 50):
    poi = query_yelp_for_places(lat, lng, radius = 1000, limit = 50)
    
    if poi:
        print("Nearby Places of Interest:")
        for places in poi:
            print(f"Business Category: {places['categories'][0]['title']}")
            print(f"Business Name: {places['name']}")
            print(f"No of Reviews: {places['review_count']}")
            print(f"Rating: {places['rating']}")
            print(f"Business Address: {places['location']['display_address'][0]}")
            print(f"Business Contact: {places['display_phone']}")
            print("-" * 30)
    else:
        print("No Business found")

In [15]:
if bike_stations_df is not None:
    for index, row in bike_stations_df.iterrows():
        print(f"Station Name: {row['Station Name']}")
        print(f"Available Bikes: {row['Available Bikes']}")
        print(f"Empty Slots: {row['Empty Slots']}")
        print(f"Latitude: {row['Latitude']}")
        print(f"Longitude: {row['Longitude']}")
        
        yelp_places_of_interest(row['Latitude'], row['Longitude'])

Station Name: W 100 St & Manhattan Ave
Available Bikes: 33
Empty Slots: 0
Latitude: 40.795
Longitude: -73.9645


NameError: name 'query_yelp_for_places' is not defined

Put your parsed results into a DataFrame

In [17]:
restaurants = []

In [18]:
if bike_stations1_df is not None:
    for index, row in bike_stations1_df.iterrows():
    results = query_yelp_for_places(row['Latitude'], row['Longitude'], radius = 1000, limit = 50)
        
        for each in results:
            if each['categories']:
                Category = each['categories'][0]['title']
            if each['name']:
                Name = each['name']
            if each['review_count']:
                Count_of_Reviews = each['review_count']
            if each['rating']:
                Rating = each['rating']
            if each['location']['display_address']:
                Address = each['location']['display_address'][0]
            if each['display_phone']:
                Contact = each['display_phone']
                
            restaurants.append({'Station Name': row['Station Name'], 'Station Latitude': row['Latitude'], 'Station Longitude': row['Lo

SyntaxError: unterminated string literal (detected at line 19) (3599427806.py, line 19)

In [18]:
if bike_stations1_df is not None:
    for index, row in bike_stations1_df.iterrows():
        results = query_yelp_for_places(row['Latitude'], row['Longitude'], radius = 1000, limit = 50)
        
        for each in results:
            if each['categories']:
                Category = each['categories'][0]['title']
            if each['name']:
                Name = each['name']
            if each['review_count']:
                Count_of_Reviews = each['review_count']
            if each['rating']:
                Rating = each['rating']
            if each['location']['display_address']:
                Address = each['location']['display_address'][0]
            if each['display_phone']:
                Contact = each['display_phone']
                
            restaurants.append({'Station Name': row['Station Name'], 'Station Latitude': row['Latitude'], 'Station Longitude': row['Longitude'], 'Business Category': Category, 'Business Name': Name, 'Rating': Rating, 'Number of Reviews': Count_of_Reviews, 'Address': Address, 'Contact': Contact})

In [19]:
yelp_business_df = pd.DataFrame(restaurants)

In [20]:
yelp_business_df.to_csv('yelp_business.csv')

# Comparing Results

Which API provided you with more complete data? Provide an explanation. 

Yelp API provided me with a lot more data than Four Square API. I was only able to extract three data points from Four Square: The business name, category and location. Other data provided does not provide any value to the current exercise. On the other hand, Yelp offers additional information such as the number of reviews, the rating, type of transactions offered (pick up or delivery), the currency accepted and a phone number to contact the business.

Get the top 10 restaurants according to their rating

In [21]:
Top_10_Restaurants = yelp_business_df.sort_values(by='Rating', ascending = False).head(10)
print(Top_10_Restaurants)

                    Station Name  Station Latitude  Station Longitude  \
4866               48 Ave & 5 St         40.744363         -73.955873   
3926         Leonard Gordon Park         40.745910         -74.057271   
7717   Wyckoff Av & Jefferson St         40.707165         -73.923711   
3957                 Astor Place         40.719282         -74.071262   
7721  Bushwick Ave & McKibbin St         40.705517         -73.939360   
3955                 Astor Place         40.719282         -74.071262   
2042      Humboldt St & Varet St         40.703172         -73.940636   
9301           E 2 St & Avenue C         40.720874         -73.980858   
3951                 Astor Place         40.719282         -74.071262   
7052    Lexington Ave & E 120 St         40.801307         -73.939817   

     Business Category      Business Name  Rating  Number of Reviews  \
4866     Mediterranean           4747 LIC     5.0                 19   
3926             Delis   Andrea Salumeria     5.0   